This is meant to reproduce the "GAF cones" notebook result using the new libraries because the results from `random_cones` appears somewhat different.

In [2]:
%load_ext autoreload
%autoreload 2

In [1]:
# Load Packages
import jax.numpy as jnp
from plotly.subplots import make_subplots

# Load Custom Modules
from plots import plot_true_function, add_optimization_path
from core import optimize_function, initial_point
from problems import get_function_by_name

In [4]:
# Define Constants
X_MIN, X_MAX, X_POINTS = -10, 10, 100
Y_MIN, Y_MAX, Y_POINTS = -10, 10, 100

x = jnp.linspace(X_MIN, X_MAX, X_POINTS)
y = jnp.linspace(Y_MIN, Y_MAX, Y_POINTS)

# Randomly sample initial point
pi = initial_point(42, minval=-10, maxval=10)

# Set Seeds for generating random samples during optimization
seed = 42

# Set Function
fn = get_function_by_name('cone')

# Set Noise Parameters
true_params = (0, 0, 1)
noise_params = (20, 20, 1)

LEARNING_RATE = 0.5
STEPS = 50

NOISE_CASES = [0.0, 5.0, 10.0, 20.0]

In [24]:
# Create Figure with SGD on random cones

BATCH_SIZES = [1, 3, 7, 10]

cfig = make_subplots(rows=len(BATCH_SIZES), cols=len(NOISE_CASES))
cfig.update_layout(height=400*len(BATCH_SIZES), width=400*len(NOISE_CASES), title_text="SGD on Random Cones", title_x=0.5)

data = []

for i, bs in enumerate(BATCH_SIZES):
    for j, n in enumerate(NOISE_CASES):
        p_sgd = optimize_function(fn, pi, true_params, [n, n, 0.], steps=STEPS, learning_rate=LEARNING_RATE, batch_size=bs, method='sgd', seed=seed)
        data.append(p_sgd)
        fig = plot_true_function(x, y, lambda x: fn(x, true_params))
        add_optimization_path(fig, p_sgd)
    
        cfig.add_trace(fig.data[0], row=i+1, col=j+1)
        cfig.add_trace(fig.data[1], row=i+1, col=j+1)
        # Hack to add titles post-facto
        cfig.add_annotation(text=f"<b>Batch Size: {bs}, Noise: {n}</b>", x=0.5, y=1.05, xref="x domain",yref="y domain", showarrow=False, row=i+1, col=j+1)

cfig.show()